In [2]:
! pip install psycopg2-binary boto3

Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.0/3.0 MB 95.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.6/139.6 kB 386.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.5/13.5 MB 116.3 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.4/84.4 kB 231.5 MB/s eta 0:00:00


In [3]:
import psycopg2
import boto3
from psycopg2.extras import RealDictCursor
import json
import logging
from typing import List, Dict

In [4]:

# Set up logging
logging.basicConfig(level=logging.INFO, format='%(asctime)s - %(levelname)s - %(message)s')
logger = logging.getLogger(__name__)

# Database connection parameters for the Dockerized PostgreSQL
DB_CONFIG = {
    'dbname': 'clinmatch_aact',
    'user': 'postgres',
    'password': 'password',  # Matches the password set in Docker
    'host': 'localhost',     # Container port mapped to host
    'port': '5432'           # Default PostgreSQL port mapped to host
}

In [5]:
def connect_to_db():
    """Establishes a connection to the PostgreSQL database in the Docker container."""
    try:
        conn = psycopg2.connect(**DB_CONFIG)
        logger.info("Successfully connected to the database")
        return conn
    except Exception as e:
        logger.error(f"Failed to connect to the database: {e}")
        raise


In [8]:
def fetch_study_data(conn) -> List[Dict]:
    """Fetches clinical trial data from the database."""
    query = """
    SELECT 
        s.nct_id,
        s.official_title,
        s.brief_title,
        s.updated_at,
        dd.description AS detailed_description,
        bs.description AS brief_summary,
        e.criteria,
        ARRAY_AGG(bc.downcase_mesh_term) AS mesh_terms
    FROM studies s
    LEFT JOIN detailed_descriptions dd ON s.nct_id = dd.nct_id
    LEFT JOIN brief_summaries bs ON s.nct_id = bs.nct_id
    LEFT JOIN eligibilities e ON s.nct_id = e.nct_id
    LEFT JOIN browse_conditions bc ON s.nct_id = bc.nct_id
    GROUP BY 
        s.nct_id, s.official_title, s.brief_title, s.updated_at,
        dd.description, bs.description, e.criteria
    ORDER BY s.nct_id;
    """
    try:
        cursor = conn.cursor(cursor_factory=RealDictCursor)
        cursor.execute(query)
        results = cursor.fetchall()
        cursor.close()
        logger.info(f"Fetched {len(results)} records from the database")
        return results
    except Exception as e:
        logger.error(f"Error executing query: {e}")
        raise

In [11]:
def merge_data_to_text(record: Dict) -> str:
    """Merges a record's fields into a single text string."""
    nct_id = record['nct_id'] or ''
    official_title = record['official_title'] or ''
    brief_title = record['brief_title'] or ''
    updated_at = str(record['updated_at']) if record['updated_at'] else ''
    detailed_description = record['detailed_description'] or ''
    brief_summary = record['brief_summary'] or ''
    criteria = record['criteria'] or ''
    mesh_terms = ', '.join([term for term in (record['mesh_terms'] or []) if term]) or ''

    text = (
        f"NCT ID: {nct_id}\n"
        f"Official Title: {official_title}\n"
        f"Brief Title: {brief_title}\n"
        f"Updated At: {updated_at}\n"
        f"Detailed Description: {detailed_description}\n"
        f"Brief Summary: {brief_summary}\n"
        f"Criteria: {criteria}\n"
        f"Mesh Terms: {mesh_terms}\n"
        "----------------------------------------\n"
    )
    return text

In [9]:
conn = connect_to_db()
records = fetch_study_data(conn)

2025-04-08 17:14:42,643 - INFO - Successfully connected to the database
2025-04-08 17:15:15,940 - INFO - Fetched 533233 records from the database


In [10]:
records

[RealDictRow([('nct_id', 'NCT00000102'),
              ('official_title', None),
              ('brief_title',
               'Congenital Adrenal Hyperplasia: Calcium Channels as Therapeutic Targets'),
              ('updated_at', datetime.datetime(2025, 4, 6, 18, 1, 47, 260213)),
              ('detailed_description',
               'This protocol is designed to assess both acute and chronic effects of the calcium channel antagonist, nifedipine, on the hypothalamic-pituitary-adrenal axis in patients with congenital adrenal hyperplasia. The multicenter trial is composed of two phases and will involve a double-blind, placebo-controlled parallel design. The goal of Phase I is to examine the ability of nifedipine vs. placebo to decrease adrenocorticotropic hormone (ACTH) levels, as well as to begin to assess the dose-dependency of nifedipine effects. The goal of Phase II is to evaluate the long-term effects of nifedipine; that is, can attenuation of ACTH release by nifedipine permit a dec

In [12]:
merged_texts = [merge_data_to_text(record) for record in records[:5]]

In [13]:
merged_texts[0]

'NCT ID: NCT00000102\nOfficial Title: \nBrief Title: Congenital Adrenal Hyperplasia: Calcium Channels as Therapeutic Targets\nUpdated At: 2025-04-06 18:01:47.260213\nDetailed Description: This protocol is designed to assess both acute and chronic effects of the calcium channel antagonist, nifedipine, on the hypothalamic-pituitary-adrenal axis in patients with congenital adrenal hyperplasia. The multicenter trial is composed of two phases and will involve a double-blind, placebo-controlled parallel design. The goal of Phase I is to examine the ability of nifedipine vs. placebo to decrease adrenocorticotropic hormone (ACTH) levels, as well as to begin to assess the dose-dependency of nifedipine effects. The goal of Phase II is to evaluate the long-term effects of nifedipine; that is, can attenuation of ACTH release by nifedipine permit a decrease in the dosage of glucocorticoid needed to suppress the HPA axis? Such a decrease would, in turn, reduce the deleterious effects of glucocortico

gene: hgnc
mycancergeno.gov

In [ ]:
# AWS Lambda function details (replace with your own)
LAMBDA_REGION = 'ap-east-1'  # Your AWS region
LAMBDA_FUNCTION_NAME = 'clinmatch-dev-metamapParser'  # Your Lambda function name

def invoke_lambda(payload: Dict) -> Dict:
    """Invokes the AWS Lambda function with the given payload."""
    try:
        lambda_client = boto3.Session(aws_access_key_id='', aws_secret_access_key='').client('lambda', region_name=LAMBDA_REGION, )
        response = lambda_client.invoke(
            FunctionName=LAMBDA_FUNCTION_NAME,
            InvocationType='RequestResponse',
            Payload=json.dumps(payload)
        )
        response_payload = json.loads(response['Payload'].read().decode('utf-8'))
        logger.info("Successfully invoked Lambda function")
        return response_payload
    except Exception as e:
        logger.error(f"Error invoking Lambda function: {e}")
        raise


In [18]:
payload = {'text': merged_texts[0]}
result = invoke_lambda(payload)

2025-04-08 17:34:56,936 - INFO - Successfully invoked Lambda function


In [28]:
import pandas as pd

In [29]:
df_cancer_snomed_ct_tree = pd.read_json('./Data/SNOMED_CT_TREE.json')

In [30]:
from tqdm import tqdm

cui_df_cancer_snomed_ct_tree = [cui for cui in list(df_cancer_snomed_ct_tree['cui'])]
cui_df_cancer_snomed_ct_tree = set(cui_df_cancer_snomed_ct_tree)

for metamap_result in tqdm(result['result']): 
    metamap_result['onco_tag'] = metamap_result['cui'] in cui_df_cancer_snomed_ct_tree

100%|██████████| 47/47 [00:00<00:00, 755296.12it/s]


In [31]:
df = pd.DataFrame(result['result'])

In [32]:
df.head()

cui                                               name    group  type  \
0  C0001627                     Congenital adrenal hyperplasia  disease  dsyn   
1  C0006685                                    Calcium Channel     drug  bacs   
2  C0087111                              Therapeutic procedure     drug  topp   
3  C0231491                           Antagonist muscle action  disease  ortf   
4  C4721408  Substance with receptor antagonist mechanism o...     drug  phsu   

                                             sources  \
0  [LNC, MTH, CSP, ICD10CM, MSH, HPO, OMIM, CHV, ...   
1  [MTH, CHV, CSP, MSH, NLMSubSyn, NCI, LCH_NW, AOD]   
2  [MTH, LNC, CSP, MSH, NLMSubSyn, AOT, HL7V2.5, ...   
3      [MTH, CHV, SNMI, SNM, UWDA, SNOMEDCT_US, FMA]   
4                            [MTH, NCI, SNOMEDCT_US]   

                      matchedtext  start  length  onco_tag  
0  Congenital Adrenal Hyperplasia   50.0    30.0     False  
1                Calcium Channels   82.0    16.0     False  
2                     Therapeutic  102.0    11.0     False  
3                      antagonist  273.0    10.0     False  
4                      antagonist  273.0    10.0     False